In [30]:
import numpy as np 
from calcbsimpvol import calcbsimpvol
import QuantLib as ql
import math
import numpy as np
import pandas as pd

# 1년을 몇일로 볼것인가? 한국은 ACT 즉 실제 그 해의 일수 365로 고정한 것을 씀.
day_count = ql.Actual365Fixed() #Actual/365
calculation_date = ql.Date(30, 5, 2020)

T=[]
S=[]
K=[]
df = pd.read_csv("./123.csv")
for i in range(len(df)):
    # print(df['종목'][i][-5:])
    expiry=0
    if df['종목'][i][-9]=='0':
        if df['종목'][i][-7]=='6':
            expiry = ql.Date(11,6,2020)
        elif df['종목'][i][-7]=='7':
            expiry = ql.Date(9,7,2020)
        elif df['종목'][i][-7]=='8':
            expiry = ql.Date(13,8,2020)
        elif df['종목'][i][-7]=='9':
            expiry = ql.Date(10,9,2020)
        elif df['종목'][i][-8:-6]=='10':
            expiry = ql.Date(8,10,2020)
        elif df['종목'][i][-8:-6]=='11':
            expiry = ql.Date(12,11,2020)
        elif df['종목'][i][-8:-6]=='12':
            expiry = ql.Date(10,12,2020)
    elif df['종목'][i][-9]=='1':
        if df['종목'][i][-7]=='3':
            expiry = ql.Date(11,3,2021)
        elif df['종목'][i][-7]=='6':
            expiry = ql.Date(10,6,2021)
        elif df['종목'][i][-7]=='9':
            expiry = ql.Date(9,9,2021)
        elif df['종목'][i][-8:-6]=='12':
            expiry = ql.Date(9,12,2021)
    elif df['종목'][i][-9]=='2':
        if df['종목'][i][-7]=='3':
            expiry = ql.Date(10,3,2022)
        elif df['종목'][i][-7]=='6':
            expiry = ql.Date(9,6,2022)
        elif df['종목'][i][-7]=='9':
            expiry = ql.Date(8,9,2022)
        elif df['종목'][i][-8:-6]=='12':
            expiry = ql.Date(8,12,2022)

    T.append(round(day_count.yearFraction(calculation_date,expiry),4))
    K.append(float(df['종목'][i][-5:]))
    S.append(float(df['현재가'][i]))

In [31]:
implied_volatility=[]
for i in range(len(T)):
    s = np.asarray(263.74) # Underlying Price : Kospi200 5.21
    k = np.asarray([K[i]]) # Strike Price 
    tau = np.asarray([T[i]]) # Time to Maturity 
    r = np.asarray(1.02)  # CD91일물 금리 2020.5.21일 기준
    q = np.asarray(0.00) # Dividend Rate 
    cp = np.asarray(-1) # Option Type 
    P = np.asarray([S[i]]) # Market Price
    
    imp_vol = calcbsimpvol(dict(cp=cp, P=P, S=s, K=k, tau=tau, r=r, q=q))
    if imp_vol[0][0]>=1:
        imp_vol[0][0]=nan
     
    implied_volatility.append(imp_vol[0][0])

In [41]:
nan_index=[implied_volatility.index(x) for x in implied_volatility if str(x)=='nan']
print(K)
strike=[]
for i in range(len(K)):
    if K.count(K[i])==11:
        strike.append(K[i])
print(strike)

TM=np.asarray(T)
KP=np.asarray(K)
imp_vol=np.asarray(implied_volatility)

TM=np.delete(TM,nan_index)
KP=np.delete(KP,nan_index)
imp_vol=np.delete(imp_vol,nan_index)

print(len(TM))
print(len(KP))
print(len(imp_vol))

[160.0, 162.5, 165.0, 167.5, 170.0, 172.5, 175.0, 177.5, 180.0, 182.5, 185.0, 187.5, 190.0, 192.5, 195.0, 197.5, 200.0, 202.5, 205.0, 207.5, 210.0, 212.5, 215.0, 217.5, 220.0, 222.5, 225.0, 227.5, 230.0, 232.5, 235.0, 237.5, 240.0, 242.5, 245.0, 247.5, 250.0, 252.5, 255.0, 257.5, 260.0, 262.5, 265.0, 267.5, 270.0, 272.5, 275.0, 277.5, 280.0, 282.5, 285.0, 287.5, 290.0, 292.5, 295.0, 297.5, 300.0, 302.5, 305.0, 307.5, 310.0, 312.5, 315.0, 317.5, 320.0, 322.5, 325.0, 327.5, 330.0, 332.5, 335.0, 337.5, 340.0, 342.5, 345.0, 347.5, 350.0, 352.5, 355.0, 357.5, 360.0, 362.5, 365.0, 367.5, 370.0, 160.0, 162.5, 165.0, 167.5, 170.0, 172.5, 175.0, 177.5, 180.0, 182.5, 185.0, 187.5, 190.0, 192.5, 195.0, 197.5, 200.0, 202.5, 205.0, 207.5, 210.0, 212.5, 215.0, 217.5, 220.0, 222.5, 225.0, 227.5, 230.0, 232.5, 235.0, 237.5, 240.0, 242.5, 245.0, 247.5, 250.0, 252.5, 255.0, 257.5, 260.0, 262.5, 265.0, 267.5, 270.0, 272.5, 275.0, 277.5, 280.0, 282.5, 285.0, 287.5, 290.0, 292.5, 295.0, 297.5, 300.0, 302.5

In [22]:
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)

trace = go.Surface(x=TM, y=KP, z=imp_vol, colorscale='Jet', opacity=0.8, 
    contours_x=dict(show=True, color="black", start=0, end=4, size=(4 - 0)/50, project_x=True), contours_y=dict(show=True, color="black", start=100, end=400, size=(400 - 100)/50, project_y=True))
data = [trace] 
layout = go.Layout(title='Call Theta Surface', 
        scene={'xaxis':{'title':'Maturity'}, 'yaxis':{'title':'Spot Price'}, 'zaxis':{'title':'Theta'}}, 
        width=800, height=800, autosize=False, margin=dict(pad=0) ) 
fig = go.Figure(data=data, layout=layout) 
iplot(fig)

In [23]:
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)

trace = go.Surface(x=TM, y=KP, z=imp_vol, colorscale='Jet', opacity=0.8)
data = [trace] 
layout = go.Layout(title='Call Theta Surface', 
        scene={'xaxis':{'title':'Maturity'}, 'yaxis':{'title':'Spot Price'}, 'zaxis':{'title':'Theta'}}, 
        width=800, height=800, autosize=False, margin=dict(pad=0) ) 
fig = go.Figure(data=data, layout=layout) 
iplot(fig)

In [29]:
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from matplotlib import cm
% matplotlib inline
fig = plt.figure()
ax = fig.gca(projection='3d')

surf = ax.plot_surface(KP,TM,imp_vol, rstride=1, cstride=1, cmap=cm.coolwarm, 
                linewidth=0.1)
fig.colorbar(surf, shrink=0.5, aspect=5)

UsageError: Line magic function `%` not found.


In [43]:
X = np.arange(0,6,1.)
Y = np.reshape(X,(2,3))
print(Y)

[[0. 1. 2.]
 [3. 4. 5.]]
